In [29]:
import numpy as np

In [44]:
xdim = 4
cons_dim = 2

A = np.random.randn(cons_dim, xdim)
sample_x = np.random.randint(0,10,xdim)
b = A@sample_x
print(sample_x)
# b = np.random.randn(cons_dim)
u = np.ones(xdim)
v = np.ones(cons_dim)
# c = A.T @ np.random.randn(cons_dim) + np.random.randn(xdim)
c = np.random.random(xdim)

In [45]:
def LHS(x, u, A=A):
    return np.block([
        [np.zeros((xdim, xdim )), np.eye(xdim), A.T],
        [np.diag(u), np.diag(x), np.zeros((xdim, cons_dim))],
        [A, np.zeros((cons_dim, xdim)), np.zeros((cons_dim, cons_dim))]
        ]).astype(np.float64)

def RHS(x, u, v, t, c=c, A=A, b=b):
    return -1 * np.block([A.T@v+u-c, np.diag(x)@u-t*np.ones(xdim), A@x-b]).astype(np.float64)

def residuals(x, u, v, t, c=c, A=A, b=b):
    res = RHS(x, u, v, t, c, A, b)
    r_dual = res[:xdim]
    r_prime = res[xdim+xdim:]
    return np.linalg.norm(r_dual)**2 + np.linalg.norm(r_prime)**2

In [46]:
def solve_direction(x, u, v, t, c=c, A=A, b=b):
    
    delta = np.linalg.solve(LHS(x, u, A), RHS(x, u, v, t, c, A, b))
    # x, u, v
    return delta[:xdim], delta[xdim:xdim+xdim], delta[xdim+xdim:]

In [47]:
# set the seed
# np.random.seed()
x = x0
mu=10
t = 1
alpha, beta = 0.1, 0.8
iter_num = 0
while True:
    iter_num += 1
    # solve direction
    delta_x, delta_u, delta_v = solve_direction(x, u, v, t)
    if np.all(delta_u >= 0):
        s_max = 1
    else:
        test = np.min(-u[delta_u<0]/delta_u[delta_u<0])
        s_max = np.min([1, test])
    s=0.99*s_max
    right = np.linalg.norm(RHS(x, u, v, t))
    while True:
        print(s)
        if np.all(x + s*delta_x >= 0):
            left = np.linalg.norm(RHS(x+s*delta_x, u+s*delta_u, v+s*delta_v,t))
            if left <= (1-alpha*s)*right:
                break
            break
        else:
            s = beta*s
    print(s)
    x = x + s*delta_x
    u = u + s*delta_u
    v = v + s*delta_v
    # print(residuals(x, u, v, t))
    if residuals(x, u, v, t) <= 1e-6:
        break
    t = mu*t
print(x)

4.778754996372012e-05
3.82300399709761e-05
3.058403197678088e-05
2.4467225581424706e-05
1.9573780465139765e-05
1.5659024372111812e-05
1.2527219497689451e-05
1.0021775598151561e-05
8.01742047852125e-06
6.413936382817e-06
5.131149106253601e-06
4.104919285002881e-06
3.2839354280023046e-06
2.627148342401844e-06
2.1017186739214753e-06
1.6813749391371803e-06
1.3450999513097443e-06
1.0760799610477955e-06
8.608639688382364e-07
6.886911750705892e-07
5.509529400564714e-07
4.407623520451772e-07
3.526098816361418e-07
2.820879053089134e-07
2.2567032424713075e-07
1.805362593977046e-07
1.444290075181637e-07
1.1554320601453097e-07
9.243456481162477e-08
7.394765184929982e-08
5.915812147943986e-08
4.7326497183551893e-08
3.786119774684152e-08
3.028895819747322e-08
2.4231166557978577e-08
1.9384933246382862e-08
1.550794659710629e-08
1.2406357277685031e-08
9.925085822148026e-09
7.94006865771842e-09
6.352054926174736e-09
5.081643940939789e-09
4.065315152751831e-09
3.2522521222014653e-09
2.6018016977611724e-0

KeyboardInterrupt: 

In [ ]:
x

array([5.50916302, 1.30203977, 1.16917844, 7.38187729])

In [ ]:
[6.9011971, 1.59997108 ,3.25132539, 4.17830984]@c

8.736430087540437